In [19]:
from process_sql import tokenize

In [ ]:
#pip install -r requirements.txt

In [ ]:
import nltk
nltk.download('punkt')

In [ ]:
tokenize(r'SELECT * FROM AIRPORTS WHERE city  =  "Anthony"')

In [20]:
import pickle

dataset = None

with open("dataset/classical_test.pkl", "rb") as file:
    dataset = pickle.load(file)

In [21]:
import datasets

In [22]:
import random

random.seed(10)

random.shuffle(dataset)

train_data = dataset[:int(len(dataset) * .8)]
test_data = dataset[int(len(dataset) * .8):]

In [23]:
inputs = [ex['text'] for ex in train_data]
targets = [ex['query'] for ex in train_data]
target_db_paths = [ex['db_path'] for ex in train_data]

In [32]:
train_data

[{'text': "i'm looking for flights from SAN FRANCISCO to ATLANTA leaving before 800",
  'query': 'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;',
  'variables': [{'example': 'ATLANTA',
    'location': 'unk',
    'name': 'city_name0',
    'type': 'city_name',
    'ancestor_of_occuring_column': {('city', 'CITY_NAME')}},
   {'example': '800',
    'location': 'unk',
    'name': 'departure_time0',
    'type': 'departure_time',
    'ancestor_of_occuring_column': {('flight', 'A

In [37]:
datasets.IterableDataset([{'text': 'hmm', 'query': 'wow'}])

AttributeError: 'IterableDataset' object has no attribute 'column_names'

In [50]:
import pandas as pd 

dataset_pd = pd.DataFrame(dataset)

In [51]:
dataset_pd = dataset_pd[['text', 'query', 'variables', 'db_path']]

In [56]:
raw_dataset = datasets.Dataset.from_pandas(dataset_pd)

In [58]:
dataset_dict = datasets.DatasetDict({
    "train": raw_dataset, 
})

In [59]:
dataset_dict['train'].train_test_split(test_size=int(len(raw_dataset) * .2))

DatasetDict({
    train: Dataset({
        features: ['text', 'query', 'variables', 'db_path'],
        num_rows: 2808
    })
    test: Dataset({
        features: ['text', 'query', 'variables', 'db_path'],
        num_rows: 701
    })
})

In [60]:
dataset_dict['train'].column_names

['text', 'query', 'variables', 'db_path']

In [39]:
dataset_dict.column_names

AttributeError: 'IterableDatasetDict' object has no attribute 'column_names'

In [33]:
dataset_dict["train"].column_names

TypeError: Values in `DatasetDict` should of type `Dataset` but got type '<class 'list'>'

In [ ]:
import sklearn
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
import transformers
from transformers import PreTrainedTokenizerFast
from tokenizers import Tokenizer
from tokenizers.models import BPE
from tokenizers.trainers import BpeTrainer
from tokenizers.pre_tokenizers import Whitespace
from tokenizers import Tokenizer

In [ ]:
source_tokenizer = Tokenizer(BPE(unk_token="[UNK]"))
source_tokenizer_trainer = BpeTrainer(special_tokens=["[UNK]", "[PAD]", "[BOS]", "[EOS]"])
source_tokenizer.pre_tokenizer = Whitespace()

source_iterator = (item for item in train_data)
source_tokenizer.train_from_iterator(
    source_iterator,
    trainer=source_tokenizer_trainer,
)

source_tokenizer = transformers.PreTrainedTokenizerFast(
    tokenizer_object=source_tokenizer,
    bos_token="[BOS]",
    eos_token="[EOS]",
    pad_token="[PAD]",
)

In [ ]:
source_tokenizer(inputs, max_length=100, truncation=True)

In [ ]:
target_vectorizer = CountVectorizer(lowercase=True, tokenizer=tokenize)

In [ ]:
target_vectorizer = target_vectorizer.fit(targets)

In [ ]:
targets_vectorized = target_vectorizer.transform(targets)

In [ ]:
target_vectorizer.transform(['return me the papers on PVLDB']).toarray()

In [ ]:
target_vectorizer.vocabulary_

In [ ]:
len(target_vectorizer.vocabulary_)

In [ ]:
word_id_tups = list(target_vectorizer.vocabulary_.items())

word_id_tups

In [ ]:
import numpy as np

(target_vectorizer.transform(targets) > 0).nonzero()

In [6]:
def build_ids_vector(targets):
    arr = []
    for row in target_vectorizer.transform(targets).toarray():
        arr.append([0] + (row > 0).nonzero()[0])

    return arr

In [7]:
build_ids_vector(targets)

NameError: name 'target_vectorizer' is not defined

In [ ]:
targets[200]

In [ ]:
target_db_paths[20]

In [ ]:
targets[300].strip()

In [ ]:
targets[0].strip()

In [ ]:
targets[23].strip().replace('(', '').replace(')', ''))

In [ ]:
tokenize(targets[20].replace(',', ' '))

In [10]:
for key in schema.schema:
    print(key)

aircraft
airline
airport
airport_service
city
class_of_service
code_description
compartment_class
date_day
days
dual_carrier
equipment_sequence
fare
fare_basis
flight
flight_fare
flight_leg
flight_stop
food_service
ground_service
month
restriction
state
time_interval
time_zone


In [7]:
targets[0].strip()

'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;'

In [9]:
tokenize(targets[0])

['select',
 'distinct',
 'flightalias0.flight_id',
 'from',
 'airport_service',
 'as',
 'airport_servicealias0',
 ',',
 'airport_service',
 'as',
 'airport_servicealias1',
 ',',
 'city',
 'as',
 'cityalias0',
 ',',
 'city',
 'as',
 'cityalias1',
 ',',
 'flight',
 'as',
 'flightalias0',
 'where',
 '(',
 'cityalias1.city_code',
 '=',
 'airport_servicealias1.city_code',
 'and',
 'cityalias1.city_name',
 '=',
 '"ATLANTA"',
 'and',
 'flightalias0.departure_time',
 '<',
 '800',
 'and',
 'flightalias0.to_airport',
 '=',
 'airport_servicealias1.airport_code',
 ')',
 'and',
 'cityalias0.city_code',
 '=',
 'airport_servicealias0.city_code',
 'and',
 'cityalias0.city_name',
 '=',
 '"SAN FRANCISCO"',
 'and',
 'flightalias0.from_airport',
 '=',
 'airport_servicealias0.airport_code',
 ';']

In [ ]:
#error col 9 (

In [33]:
len(targets)
#567

2807

In [9]:
sql_vocab = [
    'select', 'from', 'where', 'group', 'order', 'limit', 'intersect', 'union', 'except', 'by', 'having', 'distinct',
    'join', 'on', 'as', 'outer', 'inner',
    'not', 'between', '=', '>', '<', '>=', '<=', '!=', 'in', 'like', 'is', 'exists',
    'none', 'max', 'min', 'count', 'sum', 'avg',
    'and', 'or',
    'intersect', 'union', 'except',
    'desc', 'asc',
    ',', '(', ')', ';', '*'
]

In [10]:
BOS_INDEX = 0
UNK_INDEX = 1
EOS_INDEX = len(sql_vocab) + 2
PAD_INDEX = len(sql_vocab) + 3

In [11]:
def build_sql_id_vector(str):
    tokens = tokenize(str.lower())

    ids = []
    for token in tokens:
        if token in sql_vocab:
            ids.append(sql_vocab.index(token) + 2)
        else:
            ids.append(UNK_INDEX)
    return ids

In [12]:
sql_ids = []

for ex in targets:
    sql_ids.append(build_sql_id_vector(ex))

In [13]:
targets[30]

'SELECT DISTINCT COUNT( CITEalias0.CITINGPAPERID ) , WRITESalias1.AUTHORID FROM AUTHOR AS AUTHORalias0 , CITE AS CITEalias0 , WRITES AS WRITESalias0 , WRITES AS WRITESalias1 WHERE AUTHORalias0.AUTHORNAME = "Luke Zettlemoyer" AND WRITESalias0.AUTHORID = AUTHORalias0.AUTHORID AND WRITESalias0.PAPERID = CITEalias0.CITEDPAPERID AND WRITESalias1.PAPERID = CITEalias0.CITINGPAPERID GROUP BY WRITESalias1.AUTHORID ORDER BY COUNT( CITEalias0.CITINGPAPERID ) DESC ;'

In [11]:
tokenize(targets[30])

['select',
 'distinct',
 'count',
 '(',
 'citealias0.citingpaperid',
 ')',
 ',',
 'writesalias1.authorid',
 'from',
 'author',
 'as',
 'authoralias0',
 ',',
 'cite',
 'as',
 'citealias0',
 ',',
 'writes',
 'as',
 'writesalias0',
 ',',
 'writes',
 'as',
 'writesalias1',
 'where',
 'authoralias0.authorname',
 '=',
 '"Luke Zettlemoyer"',
 'and',
 'writesalias0.authorid',
 '=',
 'authoralias0.authorid',
 'and',
 'writesalias0.paperid',
 '=',
 'citealias0.citedpaperid',
 'and',
 'writesalias1.paperid',
 '=',
 'citealias0.citingpaperid',
 'group',
 'by',
 'writesalias1.authorid',
 'order',
 'by',
 'count',
 '(',
 'citealias0.citingpaperid',
 ')',
 'desc',
 ';']

In [14]:
sql_ids[30]

[2,
 13,
 34,
 45,
 1,
 46,
 44,
 1,
 3,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 44,
 1,
 16,
 1,
 4,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 37,
 1,
 21,
 1,
 5,
 11,
 1,
 6,
 11,
 34,
 45,
 1,
 46,
 42,
 47]

In [17]:
import utils

padded_sql_ids = utils.pad(sql_ids, PAD_INDEX)

In [18]:
padded_sql_ids

tensor([[ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 34, 45,  ..., 50, 50, 50],
        ...,
        [ 2, 13,  1,  ..., 50, 50, 50],
        [ 2, 34, 45,  ..., 50, 50, 50],
        [ 2, 13,  1,  ..., 50, 50, 50]])

In [23]:
build_sql_id_vector('SELECT * FROM AIRPORTS WHERE city  =  "Anthony"')

[2, 47, 3, 1, 4, 1, 20, 1]

In [24]:
dataset

[{'text': "i'm looking for flights from SAN FRANCISCO to ATLANTA leaving before 800",
  'query': 'SELECT DISTINCT FLIGHTalias0.FLIGHT_ID FROM AIRPORT_SERVICE AS AIRPORT_SERVICEalias0 , AIRPORT_SERVICE AS AIRPORT_SERVICEalias1 , CITY AS CITYalias0 , CITY AS CITYalias1 , FLIGHT AS FLIGHTalias0 WHERE ( CITYalias1.CITY_CODE = AIRPORT_SERVICEalias1.CITY_CODE AND CITYalias1.CITY_NAME = "ATLANTA" AND FLIGHTalias0.DEPARTURE_TIME < 800 AND FLIGHTalias0.TO_AIRPORT = AIRPORT_SERVICEalias1.AIRPORT_CODE ) AND CITYalias0.CITY_CODE = AIRPORT_SERVICEalias0.CITY_CODE AND CITYalias0.CITY_NAME = "SAN FRANCISCO" AND FLIGHTalias0.FROM_AIRPORT = AIRPORT_SERVICEalias0.AIRPORT_CODE ;',
  'variables': [{'example': 'ATLANTA',
    'location': 'unk',
    'name': 'city_name0',
    'type': 'city_name',
    'ancestor_of_occuring_column': {('city', 'CITY_NAME')}},
   {'example': '800',
    'location': 'unk',
    'name': 'departure_time0',
    'type': 'departure_time',
    'ancestor_of_occuring_column': {('flight', 'A

In [7]:
from process_sql import get_sql, get_schema, Schema
import os

num = 0

schema = Schema(get_schema(target_db_paths[num]))
sql = get_sql(schema, targets[num])

sql

{'from': {'table_units': [('table_unit', '__airport_service__'),
   ('table_unit', '__airport_service__'),
   ('table_unit', '__city__'),
   ('table_unit', '__city__'),
   ('table_unit', '__flight__')],
  'conds': []},
 'select': (True, [(0, (0, (0, '__flight.flight_id__', False), None))]),
 'where': [(False,
   2,
   (0, (0, '__city.city_code__', False), None),
   (0, '__airport_service.city_code__', False),
   None),
  'and',
  (False, 2, (0, (0, '__city.city_name__', False), None), '"ATLANTA"', None),
  'and',
  (False, 4, (0, (0, '__flight.departure_time__', False), None), 800.0, None),
  'and',
  (False,
   2,
   (0, (0, '__flight.to_airport__', False), None),
   (0, '__airport_service.airport_code__', False),
   None)],
 'groupBy': [],
 'having': [],
 'orderBy': [],
 'limit': None,
 'intersect': None,
 'union': None,
 'except': None}

In [ ]:
glist[405]

In [ ]:

with open('dataset/classical_test_gold.txt') as f:
    gseq_one = []
    glist = []

    for l in f.readlines():
        glist.append(l.strip())
    
    print(glist[0])

In [ ]:
glist[405]

In [ ]:
schema.idMap